In [1]:
!pip install pymongo

In [2]:
import pymongo
from pymongo import MongoClient
# importing ObjectId from bson library
from bson.objectid import ObjectId
from pprint import pprint
from datetime import datetime, date
from pymongo.mongo_client import MongoClient
from pymongo.server_api import ServerApi

In [3]:
# connect to the MongoDB server
client = MongoClient("localhost", 27017)

In [4]:
# List the available databases
for dbn in client.list_database_names():
    print('\t%s' % dbn)


	admin
	config
	demo
	local
	mongodbVSCodePlaygroundDB
	people-bson
	sample_library
	sample_mflix
	sample_pictures
	sample_school
	samples
	stocks
	test
	twitter


In [5]:
# Choose the test collection & drop it to be safe
db = client.test
db.task.drop()

In [6]:
# Prepare & add all the pending tasks
mylist = [
    {
    "description": "Write lesson plan",
    "due_date":  date(2002, 12, 4).isoformat(),
    "owner": ObjectId("AAF1AAF1AAF1AAF1AAF1AAF1")
  },
  {
    "description": "Create slides",
    "due_date":  date(2002, 12, 4).isoformat(),
    "owner":   ObjectId("AB1CAB1CAB1CAB1CAB1CAB1C")
  },
  {
    "description": "Build homework",
    "due_date":  date(2002, 12, 4).isoformat(),
    "owner": ObjectId("AAF1AAF1AAF1AAF1AAF1AAF1")
  },
  {
    "description": "Copy worksheets",
    "due_date":  date(2002, 12, 4).isoformat()
  }
]

In [7]:
db.task.insert_many(mylist)

InsertManyResult([ObjectId('67bf72a609e0002fcb4dacad'), ObjectId('67bf72a609e0002fcb4dacae'), ObjectId('67bf72a609e0002fcb4dacaf'), ObjectId('67bf72a609e0002fcb4dacb0')], acknowledged=True)

In [8]:
# Show the pending tasks
iter = db.task.find()

In [9]:
# Show all the ObjectId's along just for fun
for item in iter:
    # FYI: how to print an ObjectId:
    # print("ObjectId: {} ".format(item.get('_id')), end='')
    pprint(item)

{'_id': ObjectId('67bf72a609e0002fcb4dacad'),
 'description': 'Write lesson plan',
 'due_date': '2002-12-04',
 'owner': ObjectId('aaf1aaf1aaf1aaf1aaf1aaf1')}
{'_id': ObjectId('67bf72a609e0002fcb4dacae'),
 'description': 'Create slides',
 'due_date': '2002-12-04',
 'owner': ObjectId('ab1cab1cab1cab1cab1cab1c')}
{'_id': ObjectId('67bf72a609e0002fcb4dacaf'),
 'description': 'Build homework',
 'due_date': '2002-12-04',
 'owner': ObjectId('aaf1aaf1aaf1aaf1aaf1aaf1')}
{'_id': ObjectId('67bf72a609e0002fcb4dacb0'),
 'description': 'Copy worksheets',
 'due_date': '2002-12-04'}


In [10]:
# Choose the person collection and drop it to be safe
db.person.drop()

In [11]:
# Prepare & add all the employees
mylist = [
    {
    "name": "Kate Miller"
  },
  {
    "name": "Jack Munster"
  },
  {
    "name": "Ian Mycroft"
  }
]

In [12]:
db.person.insert_many(mylist)

InsertManyResult([ObjectId('67bf72a609e0002fcb4dacb1'), ObjectId('67bf72a609e0002fcb4dacb2'), ObjectId('67bf72a609e0002fcb4dacb3')], acknowledged=True)

In [13]:
# List all the employees
iter = db.person.find()

In [14]:
for item in iter:
    # Show all the ObjectId's along just for fun
    # FYI: how to print an ObjectId:
    # print("ObjectId: {} ".format(item.get('_id')), end='')
    pprint(item)

{'_id': ObjectId('67bf72a609e0002fcb4dacb1'), 'name': 'Kate Miller'}
{'_id': ObjectId('67bf72a609e0002fcb4dacb2'), 'name': 'Jack Munster'}
{'_id': ObjectId('67bf72a609e0002fcb4dacb3'), 'name': 'Ian Mycroft'}


In [15]:
## Assign Kate some tasks
db.person.find_one({"name": "Kate Miller"})

{'_id': ObjectId('67bf72a609e0002fcb4dacb1'), 'name': 'Kate Miller'}

In [16]:
# Get an unassigned task
task_id = db.task.find_one({"owner": { "$exists": False}})

In [17]:
# Assign it to Kate
db.person.update_one({"name": "Kate Miller"}, { "$push": {"task": task_id}})
owner_id = db.person.find_one({"name": "Kate Miller"})
db.task.update_one({"_id": task_id}, {"$set": {"owner": owner_id}}) 

UpdateResult({'n': 0, 'nModified': 0, 'ok': 1.0, 'updatedExisting': False}, acknowledged=True)

In [18]:
# assign another task to Kate
task_id = db.task.find_one({"owner": { "$exists": False}})
db.person.update_one({"name": "Kate Miller"}, { "$push": {"task": task_id}})
db.task.update_one({"_id": task_id}, {"$set": {"owner": owner_id}})

UpdateResult({'n': 0, 'nModified': 0, 'ok': 1.0, 'updatedExisting': False}, acknowledged=True)

In [19]:
# assign one to Ian also
task_id = db.task.find_one({"owner": { "$exists": False}})
db.person.update_one({"name": "Ian Mycroft"}, { "$push": {"task": task_id}})

owner_id = db.person.find_one({"name": "Ian Mycroft"})
db.task.update_one({"_id": task_id}, {"$set": {"owner": owner_id}})

UpdateResult({'n': 0, 'nModified': 0, 'ok': 1.0, 'updatedExisting': False}, acknowledged=True)

In [20]:
# Show everyone who has tasks
iter = db.person.find({"owner": { "$exists": True}})
for item in iter:
    pprint(item)

In [28]:
# Show the unassigned tasks
iter = db.task.find({"owner": { "$exists": False}})
for item in iter:
    #print(item)
    print(getattr(item, 'description'))

AttributeError: 'dict' object has no attribute 'description'

In [ ]:
# Show Kate's tasks
iter = db.person.find({"name": "Kate Miller", "task": {"$exists": True}})
for item in iter:
    pprint(item)

In [ ]:
# Show who has no tasks
iter = db.person.find({"task": {"$exists": False}})
for item in iter:
    pprint(item)